In [14]:
import pandas as pd
import cv2
from tqdm import tqdm

In [15]:
dataframes = [
    "../data/dataset-unfiltered.parquet",
    "../data/dataset.parquet",
]
df_path = dataframes[1]

In [16]:
df = pd.read_parquet(df_path)

In [17]:
display(df.head())

video_id  frame_idx  timestamp   
0  8Ilh1ewceco        145        5.0  \
1  8Ilh1ewceco        290       10.0   
2  8Ilh1ewceco        435       15.0   
3  8Ilh1ewceco        580       20.0   
4  8Ilh1ewceco        725       25.0   

                                        base64_image     dim_0     dim_1   
0  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH...  0.009040  0.003338  \
1  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH...  0.004891  0.006527   
2  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH... -0.022159  0.020703   
3  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH... -0.015903  0.033545   
4  b'/9j/4AAQSkZJRgABAQAAAQABAAD/2wBDAAgGBgcGBQgH... -0.010193 -0.012323   

      dim_2     dim_3     dim_4     dim_5  ...   dim_502   dim_503   dim_504   
0  0.029684 -0.033058  0.040864 -0.006447  ...  0.033575 -0.019076  0.047166  \
1  0.004417 -0.000323  0.006400 -0.024191  ... -0.043122 -0.010695  0.005672   
2 -0.021607 -0.019721 -0.006067 -0.035070  ... -0.017047 -0.018341 -0.006733   
3  0.009257 -0.033540  0.010586 -0.028067  ... -0.016532  0.012388  0.020868   
4  0.023012 -0.015893  0.047041  0.050783  ... -0.024013 -0.009684 -0.035481   

    dim_505   dim_506   dim_507   dim_508   dim_509   dim_510   dim_511  
0 -0.010574 -0.018608 -0.013465 -0.020017  0.086240 -0.029653  0.035949  
1  0.000172 -0.014442 -0.014647 -0.016840  0.100285  0.013794  0.015046  
2 -0.007040 -0.008368  0.009755 -0.045662  0.116601 -0.000572 -0.000985  
3 -0.012635  0.010914  0.009203 -0.010078  0.063971 -0.038024  0.025840  
4 -0.024743 -0.009812  0.035214 -0.008957  0.124215 -0.012410  0.040907  

[5 rows x 516 columns]

In [18]:
# wierdly all the timestamps are rounded to the nearest second o.O
(df["timestamp"].apply(lambda x: x % 1) == 0).sum()

60844

In [19]:
video_fps = {}
for video_id in tqdm(df.video_id.unique()):
    video_path = f"../data/videos/{video_id}.mp4"
    cap = cv2.VideoCapture(str(video_path))
    num_video_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    fps = cap.get(cv2.CAP_PROP_FPS)
    video_fps[video_id] = fps

100%|██████████| 1417/1417 [00:02<00:00, 626.05it/s]


In [20]:
def correct_timestamp(row):
    # pd.Series([1, 2], index=['foo', 'bar'])
    video_id = row["video_id"]
    frame_idx = row["frame_idx"]
    fps = video_fps[video_id]
    timestamp = frame_idx / fps
    return timestamp


df["timestamp"] = df.apply(correct_timestamp, axis=1)

In [22]:
df.to_parquet(df_path, index=False)